# Fastpages Notebook 博客示例

> fastai的项目fastpages，可以直接将 Jupyter notebooks以博客发布

- toc: true 
- badges: true
- comments: true
- categories: [jupyter]
- image: images/chart-preview.png

# 简介

以下内容演示[fastpages](https://github.com/fastai/fastpages)处理notebook的能力


在你的`fastpages`代码仓库中，将jupyter notebook保存到`_notebooks`文件夹并提交到master分支，就可以借助GitHub的actions自己生成Jekyll博客啦！


## Front matter模板设置

Jupyter Notebook第一个单元格，或markdown文件的最前面需要配置metadata。示例如下：

```
# "My Title"
> "Awesome summary"

- toc: true- branch: master- badges: true
- comments: true
- author: Hamel Husain & Jeremy Howard
- categories: [fastpages, jupyter]
```

- `toc: true` 自动生成目录
- `badges: true` 自动配置带徽章的GitHub、ninder和Google Colab链接
- `comments: true` 支持github issue评论，借助[utterances](https://github.com/utterance/utterances)实现

如果标题中包含特殊字符（如冒号），可以用双引号括起来。关于Front matter的更多详情参考[front matter section](https://github.com/fastai/fastpages#front-matter-related-options)的README文件。

## Markdown快捷方式

在单元格上方加`#hide`，**可以在博客中同时隐藏输入和输出**

在单元格上方加`#hide_input`**在博客中仅隐藏输入**

In [1]:
#hide_input
print('The comment #hide_input was used to hide the code that produced this.')

The comment #hide_input was used to hide the code that produced this.


在单元格上方加`#collapse-hide`可以实现默认**隐藏**内容的控件，点击按钮可以显示：

In [6]:
#collapse-hide
import pandas as pd
import altair as alt

在单元格上方加`#collapse-show`可以实现默认**显示**内容的控件，点击按钮可以隐藏：

In [4]:
#collapse-show
cars = 'https://vega.github.io/vega-datasets/data/cars.json'
movies = 'https://vega.github.io/vega-datasets/data/movies.json'
sp500 = 'https://vega.github.io/vega-datasets/data/sp500.csv'
stocks = 'https://vega.github.io/vega-datasets/data/stocks.csv'
flights = 'https://vega.github.io/vega-datasets/data/flights-5k.json'

## 与Altair交互

Altair支持交互图形，下面示例取自[项目](https://github.com/uwdata/visualization-curriculum)，都在[这个notebook](https://github.com/uwdata/visualization-curriculum/blob/master/altair_interaction.ipynb)里面。

In [5]:
# hide
df = pd.read_json(movies) # load movies data
genres = df['Major_Genre'].unique() # get unique field values
genres = list(filter(lambda d: d is not None, genres)) # filter out None values
genres.sort() # sort alphabetically

In [4]:
#hide
mpaa = ['G', 'PG', 'PG-13', 'R', 'NC-17', 'Not Rated']

### 示例 1: DropDown

In [5]:
# single-value selection over [Major_Genre, MPAA_Rating] pairs
# use specific hard-wired values as the initial selected values
selection = alt.selection_single(
    name='Select',
    fields=['Major_Genre', 'MPAA_Rating'],
    init={'Major_Genre': 'Drama', 'MPAA_Rating': 'R'},
    bind={'Major_Genre': alt.binding_select(options=genres), 'MPAA_Rating': alt.binding_radio(options=mpaa)}
)
  
# scatter plot, modify opacity based on selection
alt.Chart(movies).mark_circle().add_selection(
    selection
).encode(
    x='Rotten_Tomatoes_Rating:Q',
    y='IMDB_Rating:Q',
    tooltip='Title:N',
    opacity=alt.condition(selection, alt.value(0.75), alt.value(0.05))
)

alt.Chart(...)

### 示例 2: Tooltips

In [6]:
alt.Chart(movies).mark_circle().add_selection(
    alt.selection_interval(bind='scales', encodings=['x'])
).encode(
    x='Rotten_Tomatoes_Rating:Q',
    y=alt.Y('IMDB_Rating:Q', axis=alt.Axis(minExtent=30)), # use min extent to stabilize axis title placement
    tooltip=['Title:N', 'Release_Date:N', 'IMDB_Rating:Q', 'Rotten_Tomatoes_Rating:Q']
).properties(
    width=600,
    height=400
)

alt.Chart(...)

### 示例 3: More Tooltips

In [7]:
# select a point for which to provide details-on-demand
label = alt.selection_single(
    encodings=['x'], # limit selection to x-axis value
    on='mouseover',  # select on mouseover events
    nearest=True,    # select data point nearest the cursor
    empty='none'     # empty selection includes no data points
)

# define our base line chart of stock prices
base = alt.Chart().mark_line().encode(
    alt.X('date:T'),
    alt.Y('price:Q', scale=alt.Scale(type='log')),
    alt.Color('symbol:N')
)

alt.layer(
    base, # base line chart
    
    # add a rule mark to serve as a guide line
    alt.Chart().mark_rule(color='#aaa').encode(
        x='date:T'
    ).transform_filter(label),
    
    # add circle marks for selected time points, hide unselected points
    base.mark_circle().encode(
        opacity=alt.condition(label, alt.value(1), alt.value(0))
    ).add_selection(label),

    # add white stroked text to provide a legible background for labels
    base.mark_text(align='left', dx=5, dy=-5, stroke='white', strokeWidth=2).encode(
        text='price:Q'
    ).transform_filter(label),

    # add text labels for stock prices
    base.mark_text(align='left', dx=5, dy=-5).encode(
        text='price:Q'
    ).transform_filter(label),
    
    data=stocks
).properties(
    width=700,
    height=400
)

alt.LayerChart(...)

## 表格

notebook代码生成表格可以直接在博客中显示：

In [11]:
movies = 'https://vega.github.io/vega-datasets/data/movies.json'
df = pd.read_json(movies)
# display table with pandas
df[['Title', 'Worldwide_Gross', 
    'Production_Budget', 'Distributor', 'MPAA_Rating', 'IMDB_Rating', 'Rotten_Tomatoes_Rating']].head()

Title  Worldwide_Gross  Production_Budget Distributor  \
0              The Land Girls         146083.0          8000000.0    Gramercy   
1      First Love, Last Rites          10876.0           300000.0      Strand   
2  I Married a Strange Person         203134.0           250000.0   Lionsgate   
3        Let's Talk About Sex         373615.0           300000.0   Fine Line   
4                        Slam        1087521.0          1000000.0     Trimark   

  MPAA_Rating  IMDB_Rating  Rotten_Tomatoes_Rating  
0           R          6.1                     NaN  
1           R          6.9                     NaN  
2        None          6.8                     NaN  
3        None          NaN                    13.0  
4           R          3.4                    62.0

## 图像

### 本地图像


可以引用本地图片，它们会被自动复制并在博客中渲染。可以用markdown实现：

`![](my_icons/fastai_logo.png)`

![](my_icons/fastai_logo.png)

### 远程图片

远程图片语法如下：

`![](https://image.flaticon.com/icons/svg/36/36686.svg)`

![](https://image.flaticon.com/icons/svg/36/36686.svg)

### Gif动画

Gif动画，当日没问题！

`![](https://upload.wikimedia.org/wikipedia/commons/7/71/ChessPawnSpecialMoves.gif)`

![](https://upload.wikimedia.org/wikipedia/commons/7/71/ChessPawnSpecialMoves.gif)

### 图片说明（Caption）

图片说明可以用下面markdown语法实现：

```
![](https://www.fast.ai/images/fastai_paper/show_batch.png "Credit: https://www.fast.ai/2020/02/13/fastai-A-Layered-API-for-Deep-Learning/")
```


![](https://www.fast.ai/images/fastai_paper/show_batch.png "Credit: https://www.fast.ai/2020/02/13/fastai-A-Layered-API-for-Deep-Learning/")





# 其他元素

## GitHub Flavored Emojis

输入 `I give this post two :+1:!` 渲染颜文字：

I give this post two :+1:!

## Tweet卡片

输入 `> twitter: https://twitter.com/jakevdp/status/1204765621767901185?s=20` 渲染推文：

> twitter: https://twitter.com/jakevdp/status/1204765621767901185?s=20

## Youtube视频

输入 `> youtube: https://youtu.be/XfoYk_Z5AkI` 渲染视频：


> youtube: https://youtu.be/XfoYk_Z5AkI

## 提示文字（Boxes / Callouts ）

输入 `> Warning: There will be no second warning!` 效果：


> Warning: There will be no second warning!



输入 `> Important: Pay attention! It's important.` 效果：

> Important: Pay attention! It's important.



输入 `> Tip: This is my tip.` 效果：

> Tip: This is my tip.



输入 `> Note: Take note of this.` 效果：

> Note: Take note of this.



输入 `> Note: A doc link to [an example website: fast.ai](https://www.fast.ai/) should also work fine.` 效果：

> Note: A doc link to [an example website: fast.ai](https://www.fast.ai/) should also work fine.

## 尾注

可以在notebook里加尾注，但不是用markdown语法实现，[具体语法请看说明](https://github.com/fastai/fastpages/blob/master/_fastpages_docs/NOTEBOOK_FOOTNOTES.md)。

```
{% raw %}For example, here is a footnote {% fn 1 %}.
And another {% fn 2 %}
{{ 'This is the footnote.' | fndetail: 1 }}
{{ 'This is the other footnote. You can even have a [link](www.github.com)!' | fndetail: 2 }}{% endraw %}
```

For example, here is a footnote {% fn 1 %}.

And another {% fn 2 %}

{{ 'This is the footnote.' | fndetail: 1 }}
{{ 'This is the other footnote. You can even have a [link](www.github.com)!' | fndetail: 2 }}